In [3]:
import matplotlib.pyplot as plt
import numpy as np
from scipy.interpolate import make_interp_spline
from matplotlib import font_manager
import pandas as pd
import joblib
import argparse
import time
from matplotlib.ticker import ScalarFormatter, FuncFormatter

from params_prob import *
from ECO_function import *

debug = True  



In [4]:
## Read xlsx and dump the values to 4 variables 

def read_excel_data(filename):
    """Reads an Excel file and assigns values to variables based on column names.

    Args:
        filename (str): The path to the Excel file.

    Returns:
        tuple: A tuple containing the values for def_den, carbon_int, and epa.
    """

    try:
        # Read the Excel file into a Pandas DataFrame
        df = pd.read_excel(filename)

        # Extract values based on column names
        def_den = df['defden'].values
        carbon_int = df['CarbonInt'].values
        epa = df['EPA'].values
        gpa = df['GPA'].values

        return def_den, carbon_int, epa,gpa

    except FileNotFoundError:
        print(f"Error: File '{filename}' not found.")
        return None
    except KeyError as e:
        print(f"Error: Column '{e.args[0]}' not found in the Excel file.")
        return None

# Example usage
filename = 'example_final_params_data_50.xlsx'  # Replace with your actual file name
#filename = 'boxplot/final_box_plot/generated_files/data/final_params_data_100.xlsx'  # Replace with your actual file name
result = read_excel_data(filename)

if result:
    def_den, carbon_int, epa, gpa = result
    print("def-den:", def_den)
    print("def-den length",len(def_den))
    print("carbon_int:", carbon_int)
    print("carbon int len", len(carbon_int))
    print("epa:", epa)
    print("epa len",len(epa))
    print("gpa:", gpa)
    print("gpa len",len(gpa))

def-den: [0.1535 0.147  0.1145 0.1535 0.186  0.1535 0.121  0.3095 0.199  0.121
 0.108  0.4005 0.355  0.251  0.095  0.1795 0.1145 0.3095 0.108  0.3745
 0.1145 0.134  0.1405 0.4135 0.3485 0.1275 0.108  0.16   0.1535 0.1925
 0.1795 0.121  0.095  0.1275 0.147  0.1405 0.2055 0.147  0.1535 0.108
 0.1015 0.108  0.3875 0.095  0.186  0.134  0.147  0.108  0.186  0.134 ]
def-den length 50
carbon_int: [663.484524 647.110838 637.479258 657.705576 660.59505  645.184522
 665.41084  671.189788 683.710842 645.184522 647.110838 661.558208
 646.14768  656.742418 649.037154 649.037154 651.926628 644.221364
 672.152946 665.41084  640.368732 657.705576 654.816102 649.037154
 646.14768  648.073996 653.852944 650.96347  641.33189  645.184522
 638.442416 663.484524 637.479258 666.373998 650.96347  665.41084
 648.073996 661.558208 663.484524 658.668734 679.85821  664.447682
 644.221364 672.152946 677.931894 658.668734 647.110838 653.852944
 650.000312 637.479258]
carbon int len 50
epa: [1.13076923 0.99230769 1.

In [12]:

def run_greenfpga_asic(epa_loop,gpa_loop,dd_loop,ci_loop,napp,ndes,nlife,power,chip_area):
        #Initialize variables
        embodied_carbon = []
        operational_carbon = []
        total_carbon = []
        total_10  = []
        total_20  = []
        total_30  = []
        total_40  = []
        total_50  = []
        total_60  = []
        total_70  = []
        total_80  = []
        total_90  = []
        total_100 = []
        
        #if debug:
        #        print("-------------------------")
        #        print("napp",napp)
        #        print("ndes",ndes)
        #        print("nlife",nlife)
        #        print("power",power)
        #        print("chip_area",chip_area)
        #        print("-------------------------")

        defden_number = def_den[dd_loop]
        gpa_number = gpa[gpa_loop]
        epa_number = epa[epa_loop]
        ci_number = carbon_int[ci_loop]
        print(ci_loop)
        args = argparse.Namespace(design_dir='test_example/GPU_analysis/',
                                  des_type='ASIC',
                                  des_cfp_ty='NEW',
                                  num_app=napp,
                                  num_des=ndes,
                                  num_lifetime=nlife,
                                  power=power,
                                  chip_area=chip_area,
                                  ope_vol=1000000,
                                  emb_vol=1000000,
                                  dc_val=1,
                                  nfpga=None,
                                  node=10,
                                  mem_cap=None,
                                  uncertain_off=False,
                                  epa=epa_number,
                                  defect_density=defden_number,
                                  gpa=epa_number,
                                  carbon_intensity=ci_number)
        #embc,opec,totc = greenfpga_func(args)
        embc,opec,totc,t10,t20,t30,t40,t50,t60,t70,t80,t90,t100 = greenfpga_func(args)
        embodied_carbon.append(embc)
        operational_carbon.append(opec)
        total_carbon.append(totc)
        total_10.append(t10)
        total_20.append(t20)
        total_30.append(t30)
        total_40.append(t40)
        total_50.append(t50)
        total_60.append(t60)
        total_70.append(t70)
        total_80.append(t80)
        total_90.append(t90)
        total_100.append(t100)

        fin_df_asic = pd.DataFrame(
                            {'Emb_Carbon': embodied_carbon,
                            'Operational_Carbon': operational_carbon,
                            'Total_Carbon' : total_carbon,
                            'Total_0.1_Ope' : total_10,
                            'Total_0.2_Ope' : total_20,
                            'Total_0.3_Ope' : total_30,
                            'Total_0.4_Ope' : total_40,
                            'Total_0.5_Ope' : total_50,
                            'Total_0.6_Ope' : total_60,
                            'Total_0.7_Ope' : total_70,
                            'Total_0.8_Ope' : total_80,
                            'Total_0.9_Ope' : total_90,
                            'Total_1.0_Ope' : total_100,
                            'Loop variables' : f"epa_loop_{epa_loop}__gpa_loop_{gpa_loop}__ci_loop_{ci_loop}__dd_loop_{dd_loop}",
                            'Loop_values': f"EPA_{epa_number}__GPA_{gpa_number}__CI_{ci_number}__DefDen_{defden_number}"})

        return fin_df_asic

In [13]:
#Initialize knobs, DO NOT TOUCH 
ASIC_ASIC = False
ASIC_FPGA = False
GPU_GPU   = False 
GPU_FPGA  = False 
CPU_CPU   = False  
CPU_FPGA  = False 

#ASIC 
#ASIC_ASIC = True
#ASIC_FPGA = True

#GPU
GPU_GPU = True
GPU_FPGA = True

#CPU
#CPU_CPU = True
#CPU_FPGA = True

if ASIC_ASIC:
    NumApps_arr =     [1,2,3,4,5,6,7,8]
    NumDes_arr =      [1,2,3,4,5,6,7,8]
    NumLifetime_arr = [2,4,6,8,10,12,14,16]
    power = 10
    area = 100
    type='asic'
if ASIC_FPGA:
    NumApps_arr_fp =     [1,2,3,4,5,6,7,8]
    NumDes_arr_fp =      [1,1,1,1,1,1,1,1]
    NumLifetime_arr_fp = [2,4,6,8,10,12,14,16]
    power_fp = 30
    area_fp = 400
    type_fp='fpga_asic'

if GPU_GPU:
    #NumApps_arr =     [1,2,3,4,5,6,7,8]
    #NumDes_arr =      [1,1,2,2,3,3,4,4]
    #NumLifetime_arr = [2,4,6,8,10,12,14,16]
    NumApps_arr =     [4,8,12,16,20,24,28,32]
    NumDes_arr =      [2,4,6,8,10,12,14,16]
    NumLifetime_arr = [8,16,24,32,40,48,56,72]
    power = 116.6
    area = 48.9
    type='gpu'
if GPU_FPGA:
    #NumApps_arr_fp =     [1,2,3,4,5,6,7,8]
    #NumDes_arr_fp =      [1,1,1,1,1,1,1,1]
    #NumLifetime_arr_fp = [2,4,6,8,10,12,14,16]
    NumApps_arr_fp =     [4,8,12,16,20,24,28,32]
    NumDes_arr_fp =      [1,1,1,1,1,1,1,1]
    NumLifetime_arr_fp = [8,16,24,32,40,48,56,72]
    power_fp = 120
    area_fp = 214.89
    type_fp='fpga_gpu'
    
if CPU_CPU:
    NumApps_arr =     [1,2,3,4,5,6,7,8]
    NumDes_arr =      [1,1,1,1,1,1,1,1]
    NumLifetime_arr = [2,4,6,8,10,12,14,16]
    power = 170
    area = 214
    type='cpu'
if CPU_FPGA:
    NumApps_arr_fp =     [1,2,3,4,5,6,7,8]
    NumDes_arr_fp =      [1,1,1,1,1,1,1,1]
    NumLifetime_arr_fp = [2,4,6,8,10,12,14,16]
    power_fp = 0.9717
    area_fp = 600
    type_fp = 'fpga_cpu'

print("Parameter ranges for current device type")
print("NumApps_arr",NumApps_arr)
print("NumDes_arr",NumDes_arr)
print("NumLifetime_arr",NumLifetime_arr)
print("power",power)
print("area",area)
print("type",type)
print("-------------------------")

print("Parameter ranges for current FPGA type")
print("NumApps_arr FPGA",NumApps_arr_fp)
print("NumDes_arr FPGA",NumDes_arr_fp)
print("NumLifetime_arr FPGA",NumLifetime_arr_fp)
print("power FPGA",power_fp)
print("area FPGA",area_fp)
print("type",type_fp)
print("-------------------------")


Parameter ranges for current device type
NumApps_arr [4, 8, 12, 16, 20, 24, 28, 32]
NumDes_arr [2, 4, 6, 8, 10, 12, 14, 16]
NumLifetime_arr [8, 16, 24, 32, 40, 48, 56, 72]
power 116.6
area 48.9
type gpu
-------------------------
Parameter ranges for current FPGA type
NumApps_arr FPGA [4, 8, 12, 16, 20, 24, 28, 32]
NumDes_arr FPGA [1, 1, 1, 1, 1, 1, 1, 1]
NumLifetime_arr FPGA [8, 16, 24, 32, 40, 48, 56, 72]
power FPGA 120
area FPGA 214.89
type fpga_gpu
-------------------------


In [7]:
index = np.random.randint(0,49,(10000,4))
print(index)
for entry in index:
    print(entry[0])
    print(entry[1])
    print(entry[2])
    print(entry[3])

[[41 42 47  1]
 [30 28 18 33]
 [ 7 43  4 33]
 ...
 [36  3 40 11]
 [44 31 17 14]
 [47 31 14 40]]
41
42
47
1
30
28
18
33
7
43
4
33
23
48
20
11
46
16
7
18
22
5
5
39
30
10
19
11
37
20
28
23
44
13
38
14
8
37
34
23
2
44
18
0
32
18
3
30
37
18
14
17
9
39
18
36
37
12
9
37
30
32
41
7
13
4
27
36
48
41
36
45
25
14
46
1
42
22
11
4
3
14
13
3
5
32
17
41
32
35
2
41
28
32
8
23
48
39
19
10
9
43
25
20
38
38
7
34
33
0
29
34
13
4
3
48
28
26
17
2
33
5
3
15
38
30
26
20
32
28
15
29
18
18
36
36
41
11
38
30
48
26
38
29
40
31
33
31
29
40
34
40
40
44
41
34
30
16
24
45
33
15
35
23
24
17
27
34
13
37
47
29
1
7
37
27
14
6
16
17
21
44
8
6
45
14
44
34
6
35
39
26
42
20
8
10
39
29
15
44
16
48
20
39
13
26
38
25
14
14
10
25
41
13
25
18
6
16
32
31
5
33
48
30
32
46
5
44
43
5
40
29
18
28
37
29
38
37
9
36
42
21
0
31
2
3
22
31
29
41
3
30
33
12
28
46
23
4
44
24
25
39
7
35
19
43
47
12
43
46
14
43
21
27
11
31
38
2
41
1
15
25
23
23
34
14
25
30
28
2
26
20
42
11
16
2
12
37
1
48
6
24
44
22
27
39
44
27
35
6
28
25
6
41
36
34
46
11
28
8


In [16]:
#Constant params to send to code
print("Parameter ranges for current device type")
print("NumApps_arr",NumApps_arr)
print("NumDes_arr",NumDes_arr)
print("NumLifetime_arr",NumLifetime_arr)
print("power",power)
print("area",area)
print("type",type)
print("-------------------------")

print("Parameter ranges for current FPGA type")
print("NumApps_arr FPGA",NumApps_arr_fp)
print("NumDes_arr FPGA",NumDes_arr_fp)
print("NumLifetime_arr FPGA",NumLifetime_arr_fp)
print("power FPGA",power_fp)
print("area FPGA",area_fp)
print("type_fp",type_fp)
print("-------------------------")


# Create an empty DataFrame to store the results
total_cfp_df = pd.DataFrame()
total_cfp_df_fp = pd.DataFrame()

#For ASIC/GPU/CPU
print("Starting ASIC/GPU/CPU")
for i in range(len(NumApps_arr)):
#for i in range(0,2):
    print("i",i)
    NumApps = NumApps_arr[i]
    NumDes = NumDes_arr[i]
    NumLifetime = NumLifetime_arr[i]
    
    print("NumApps", NumApps) if debug else None
    
    #Start time
    start = time.time()

    #Run jobs in parallel
    run_values_asic = joblib.Parallel(n_jobs=-1)(joblib.delayed(run_greenfpga_asic)(entry[0],entry[1],entry[2],entry[3],napp=NumApps,ndes=NumDes,nlife=NumLifetime,power=power,chip_area=area) for entry in index)

    #Convert to DataFrame
    final_df = pd.concat(run_values_asic, ignore_index=True)
    
    if debug:
        #Dump to excel
        #final_df.to_excel(f"temp_debug_dir/CFP_data_ASIC_FPGA_Napp_{NumApps}_sample_10_asic.xlsx",index=False)
        #final_df.to_excel(f"temp_debug_dir/CFP_data_GPU_FPGA_Napp_{NumApps}_sample_10000_asic_randomsample.xlsx",index=False)
        print("Dump finish")

    # Add the 'Total_0.2_Ope' column to dist_df with the corresponding column name
    if GPU_GPU:
        total_cfp_df[f'NumApp{i}'] = final_df['Total_0.6_Ope']  
    else:
        total_cfp_df[f'NumApp{i}'] = final_df['Total_0.2_Ope']  

    end_time = time.time()  # End time for performance measurement
    elapsed_time = end_time - start
    print(f"Elapsed time for processing: {elapsed_time:.2f} seconds")
   
#FPGA
print("Starting FPGA")
for j in range(len(NumApps_arr_fp)):
#for j in range(0,2):
    print("j",j)
    NumApps_fp = NumApps_arr_fp[j]
    NumDes_fp = NumDes_arr_fp[j]
    NumLifetime_fp = NumLifetime_arr_fp[j]
   
   
    print("NumApps_fp", NumApps_fp) if debug else None
    
    #Start time
    start = time.time()

    #Run jobs in parallel
    run_values_fpga = joblib.Parallel(n_jobs=-1)(joblib.delayed(run_greenfpga_asic)(entry_fpga[0],entry_fpga[1],entry_fpga[2],entry_fpga[3],napp=NumApps_fp,ndes=NumDes_fp,nlife=NumLifetime_fp,power=power_fp,chip_area=area_fp) for entry_fpga in index)

    #Convert to DataFrame
    final_df_fp = pd.concat(run_values_fpga, ignore_index=True)
    
    if debug:
        #Dump to excel
        #final_df_fp.to_excel(f"temp_debug_dir/CFP_data_ASIC_FPGA_Napp_{NumApps_fp}_sample_10_fpga.xlsx",index=False)
        #final_df_fp.to_excel(f"temp_debug_dir/CFP_data_GPU_FPGA_Napp_{NumApps_fp}_sample_10000_fpga_randomsample.xlsx",index=False)
        print("Dump finish")

    # Add the 'Total_0.2_Ope' column to dist_df with the corresponding column name
    if GPU_GPU:
        total_cfp_df_fp[f'NumApp{j}'] = final_df_fp['Total_0.6_Ope']  
    else:
        total_cfp_df_fp[f'NumApp{j}'] = final_df_fp['Total_0.2_Ope']  

    end_time = time.time()  # End time for performance measurement
    elapsed_time = end_time - start
    print(f"Elapsed time for processing: {elapsed_time:.2f} seconds")

#if debug:
    #total_cfp_df.to_excel(f"temp_debug_dir/GPU_sample_10000_randomsample_GPUvFPGA.xlsx",index=False)
    #total_cfp_df_fp.to_excel(f"temp_debug_dir/FPGA_sample_10000_randomsample_GPUvFPGA.xlsx",index=False) 

Parameter ranges for current device type
NumApps_arr [4, 8, 12, 16, 20, 24, 28, 32]
NumDes_arr [2, 4, 6, 8, 10, 12, 14, 16]
NumLifetime_arr [8, 16, 24, 32, 40, 48, 56, 72]
power 116.6
area 48.9
type gpu
-------------------------
Parameter ranges for current FPGA type
NumApps_arr FPGA [4, 8, 12, 16, 20, 24, 28, 32]
NumDes_arr FPGA [1, 1, 1, 1, 1, 1, 1, 1]
NumLifetime_arr FPGA [8, 16, 24, 32, 40, 48, 56, 72]
power FPGA 120
area FPGA 214.89
type_fp fpga_gpu
-------------------------
Starting ASIC/GPU/CPU
i 0
NumApps 4
14
0
Testing CFP debug
Ctest_Total 30065.324046328897
Ctest_per unit 0.030065324046328896
Testing CFP debug
Ctest_Total 30734.569031751136
Ctest_per unit 0.030734569031751136
4
Testing CFP debug
Ctest_Total 30600.720034666687
Ctest_per unit 0.030600720034666688
20
1839

33
24
Testing CFP debug
Ctest_Total 29663.777055075556
Ctest_per unit 0.029663777055075558
36
35
Testing CFP debugTesting CFP debug
Ctest_Total 31136.116023004477
Ctest_per unit 0.03113611602300448

Ctest_Tot

KeyboardInterrupt: 